# Pipeline model

## Carga de los datasets enriquecidos para nuestra estrategia de entrenamiento del modelo

In [108]:
train_enriched_path = "/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/data/processed/hybrid_model/train_enriched_model.pkl"
test_enriched_path = "/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/data/processed/hybrid_model/test_enriched_model.pkl"

In [109]:
import pandas as pd 

# Cargar los datasets enriquecidos
train = pd.read_pickle(train_enriched_path)
test = pd.read_pickle(test_enriched_path)

# Confirmar las formas de los datasets cargados
print(f"Train cargado: {train.shape}")
print(f"Test cargado: {test.shape}")

# Verificar algunas filas para validar las columnas enriquecidas
print("Primeras filas de Train:")
print(train.head())

print("\nPrimeras filas de Test:")
print(test.head())


Train cargado: (36858893, 16)
Test cargado: (29275, 15)
Primeras filas de Train:
   session_id       date         timestamp_local  add_to_cart  user_id  \
0           1 2024-06-05 2024-06-05 16:55:01.465            0       -1   
1           3 2024-06-04 2024-06-04 18:40:25.285            0       -1   
2           3 2024-06-04 2024-06-04 18:40:36.684            0       -1   
3           4 2024-06-02 2024-06-02 17:30:12.605            0       -1   
4           4 2024-06-02 2024-06-02 17:30:15.647            0       -1   

   country  partnumber  device_type pagetype  session_length  \
0       57       31751            1       24               1   
1       29       35349            1       24               2   
2       29        7701            1       24               2   
3       57        5092            1       24               5   
4       57       15276            1       24               5   

   unique_products_count  product_popularity time_of_day  time_diff  \
0                 

### **Análisis de los resultados tras cargar los datasets enriquecidos**

#### **1. Formas de los datasets cargados**
- **Train**: `(36,858,893, 16)`
  - Las 16 columnas coinciden con el dataset enriquecido, incluyendo las nuevas características (`country_popularity`, `device_popularity`, etc.).
- **Test**: `(29,275, 15)`
  - Las 15 columnas coinciden con el dataset enriquecido (sin `add_to_cart`).

**Conclusión**:
- Las formas de los datasets son correctas y reflejan los enriquecimientos realizados.

---

#### **2. Validación de columnas en `Train`**
- **Columnas enriquecidas**:
  - **`country_popularity`** y **`device_popularity`** tienen valores consistentes con lo esperado, basados en la frecuencia de productos por país y dispositivo.
- **Ejemplo**:
  - `partnumber = 31751` en `country = 57` y `device_type = 1` tiene `country_popularity = 204` y `device_popularity = 623`, lo que coincide con el cálculo realizado.

**Conclusión**:
- Las columnas enriquecidas en `Train` se han cargado correctamente.

---

#### **3. Validación de columnas en `Test`**
- **Columnas enriquecidas**:
  - **`country_popularity`** y **`device_popularity`** están correctamente mapeadas desde `Train` para productos presentes en ambos datasets.
  - Productos nuevos tienen valores bajos o predeterminados (como `0` o un valor mínimo).
- **Ejemplo**:
  - `partnumber = 12639` en `country = 57` tiene `country_popularity = 225.0` y `device_popularity = 1666.0`, lo que coincide con el mapeo esperado.

**Conclusión**:
- Las columnas enriquecidas en `Test` también se han cargado correctamente.


---

## Submuestreo - 1%

In [110]:
# Submuestra del 1% de Train
train_sample = train.sample(frac=0.01, random_state=42)
print(f"Tamaño de la submuestra: {train_sample.shape}")


Tamaño de la submuestra: (368589, 16)


## Pipeline de modelado


### **Pipeline de modelado**

#### **1. Selección de características**
Con base en los enriquecimientos realizados, seleccionaremos las características más relevantes para el modelo. Excluiremos columnas como:
- `session_id`, `timestamp_local`, `date`: Son identificadores o timestamps que no aportan directamente al modelado.
- `add_to_cart` en `Train`: Se usará como objetivo, pero no como característica.


In [111]:
features = [
    'user_id', 'country', 'partnumber', 'device_type', 'pagetype', 
    'session_length', 'unique_products_count', 'product_popularity', 
    'country_popularity', 'device_popularity', 'time_of_day', 'time_diff'
]

#### **2. Codificación y preprocesamiento**
Para variables categóricas como `user_id`, `partnumber`, `pagetype`, y `time_of_day`, aplicaremos **One-Hot Encoding** o **Label Encoding** dependiendo del modelo.


In [112]:
from sklearn.preprocessing import LabelEncoder

# Variables categóricas a codificar
categorical_cols = ['user_id', 'partnumber', 'device_type', 'pagetype', 'time_of_day']

# Convertir todas las columnas categóricas a tipo string
for col in categorical_cols:
    train_sample[col] = train_sample[col].astype(str)
    test[col] = test[col].astype(str)

# Crear un LabelEncoder para cada columna categórica
label_encoders = {}
for col in categorical_cols:
    le = LabelEncoder()
    
    # Combinar datos de train_sample y test para ajustar el encoder
    combined_data = pd.concat([train_sample[col], test[col]], axis=0)
    le.fit(combined_data)
    
    # Transformar ambos datasets
    train_sample[col] = le.transform(train_sample[col])
    test[col] = le.transform(test[col])
    
    label_encoders[col] = le


In [100]:
print(train_sample[categorical_cols].head())
print(test[categorical_cols].head())


          user_id  partnumber  device_type  pagetype  time_of_day
31270269        0       10419            0         8            3
33943724        0        8595            0         8            2
27743675        0       15915            0         8            0
4380251         0       16026            0         8            0
20408367        0       24315            0         8            3
   user_id  partnumber  device_type  pagetype  time_of_day
0        0        1591            0         8            1
1        0       14172            0         8            1
2        0        1669            0         8            1
3        0        5085            0         8            1
4        0        2061            0         8            1


El valor `-1` en la columna `user_id` (que representaba usuarios no logueados) ha sido codificado como `0` tras aplicar el **LabelEncoder**. Esto ocurre porque el `LabelEncoder` asigna etiquetas numéricas consecutivas, comenzando desde `0`, y no distingue el propósito de los valores originales.

**Impacto y solución**

Si el `0` ahora representa a los usuarios no logueados, debemos:
1. **Mantener un mapeo claro**: Documentar esta correspondencia para identificar a los usuarios no logueados en análisis posteriores.
2. **Ajustar los análisis futuros**: Reemplazar o filtrar los valores `0` como no logueados donde sea necesario.

#### **Acción importante a tener en cuenta**
1. **Documentar el mapeo**:
   - `user_id == 0` → usuarios no logueados (antes `-1`).
   - Otros valores → usuarios logueados.
   
   Esto garantiza que el propósito original del dato se preserve.

2. **Validar el mapeo en los datos**:
   - Verificar que el `0` aparece exclusivamente donde antes había un `-1`.


In [113]:
# Validar cuántos usuarios no logueados (0) hay en train_sample y test
print("Usuarios no logueados en train_sample:", (train_sample['user_id'] == 0).sum())
print("Usuarios no logueados en test:", (test['user_id'] == 0).sum())

# Comparar con los valores originales de -1
original_no_logged_train = (train['user_id'] == -1).sum()
print("Usuarios no logueados originales en train:", original_no_logged_train)


Usuarios no logueados en train_sample: 313824
Usuarios no logueados en test: 23509
Usuarios no logueados originales en train: 31370215


### **3. Separar características (`X`) y objetivo (`y`)**
Ahora que las columnas categóricas están codificadas, seleccionaremos las características relevantes y el objetivo (`add_to_cart`).

In [114]:
# Separar características y objetivo
X = train_sample[features]
y = train_sample['add_to_cart']  # Objetivo binario


### 4. Dividir en conjuntos de entrenamiento y validación
Realizaremos una división del 80% para entrenamiento y 20% para validación.

In [39]:
from sklearn.model_selection import train_test_split

# División en conjuntos de entrenamiento y validación
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

print(f"Tamaño de X_train: {X_train.shape}, y_train: {y_train.shape}")
print(f"Tamaño de X_val: {X_val.shape}, y_val: {y_val.shape}")


Tamaño de X_train: (294871, 12), y_train: (294871,)
Tamaño de X_val: (73718, 12), y_val: (73718,)


### 5. Entrenar un modelo inicial - RandomForest
Entrenaremos un Random Forest como baseline para evaluar el rendimiento inicial del pipeline.

In [40]:
from sklearn.ensemble import RandomForestClassifier

# Entrenar el modelo
rf_model = RandomForestClassifier(n_estimators=100, random_state=42)
rf_model.fit(X_train, y_train)

# Predicciones en el conjunto de validación
y_pred = rf_model.predict(X_val)


#### 5.1. Evaluar el modelo inicial
Evaluaremos el rendimiento usando métricas como precisión, recall y F1-score.

In [23]:
from sklearn.metrics import classification_report, accuracy_score

# Evaluación del modelo
print("Evaluación del modelo:")
print(classification_report(y_val, y_pred))
print(f"Accuracy: {accuracy_score(y_val, y_pred):.4f}")


Evaluación del modelo:
              precision    recall  f1-score   support

           0       0.93      1.00      0.97     68412
           1       0.89      0.10      0.17      5306

    accuracy                           0.93     73718
   macro avg       0.91      0.55      0.57     73718
weighted avg       0.93      0.93      0.91     73718

Accuracy: 0.9340


#### 5.2 Análisis de las salidas

**1. Tamaño de los conjuntos de datos**
- **`X_train`**: (294,871, 12) → Tamaño razonable para entrenar un modelo base en tiempo razonable.
- **`X_val`**: (73,718, 12) → Conjunto de validación suficientemente grande para evaluar el modelo.

**2. Métricas de evaluación**
- **Clases desbalanceadas**:
  - Clase 0 (no agregó al carrito): 68,412 ejemplos → Alta precisión y recall (casi 100%).
  - Clase 1 (agregó al carrito): 5,306 ejemplos → Muy bajo recall (10%) y f1-score (17%).

- **Accuracy**:
  - **93.4%**, pero esto está impulsado principalmente por la alta precisión en la clase dominante (0).

- **Macro avg**:
  - F1-score promedio: 57% → Indica que el modelo tiene un desempeño muy bajo en la clase minoritaria (1).

**Conclusión**:
El modelo está sesgado hacia la clase mayoritaria debido al desbalance en las etiquetas.

---

**3. Tiempo de entrenamiento**
- **46 segundos**: Es razonable para esta submuestra (1%) usando Random Forest. Sin embargo, con el dataset completo, Random Forest podría volverse más costoso computacionalmente.

---

**Consideraciones sobre el modelo**
1. **Random Forest**:
   - Escala pobremente con grandes datasets porque:
     - Requiere construir múltiples árboles.
     - Cada árbol necesita analizar todo el dataset para entrenarse.
   - Podría volverse ineficiente si entrenamos con el dataset completo (`~37 millones de filas`).

2. **XGBoost** (o LightGBM):
   - Más eficiente computacionalmente para grandes datasets.
   - Permite manejar desbalance de clases mediante parámetros como `scale_pos_weight`.
   - Utiliza técnicas avanzadas como pre-podado y búsqueda más rápida en nodos.

3. **Conclusión**:
   - Random Forest es adecuado como baseline, pero XGBoost o LightGBM serían opciones superiores para el modelo final.



---

### 6. Modelo XGBoost

In [28]:
from xgboost import XGBClassifier
from sklearn.metrics import classification_report, accuracy_score

# Calcular el peso de la clase minoritaria
scale_pos_weight = y_train.value_counts()[0] / y_train.value_counts()[1]

# Configuración del modelo XGBoost
xgb_model = XGBClassifier(
    n_estimators=200,
    max_depth=10,
    learning_rate=0.1,
    scale_pos_weight=scale_pos_weight,
    random_state=42,
    eval_metric='logloss'
)


# Entrenar el modelo
xgb_model.fit(X_train, y_train)

# Predicciones en el conjunto de validación
y_pred = xgb_model.predict(X_val)

# Evaluar el modelo
print("Evaluación del modelo XGBoost:")
print(classification_report(y_val, y_pred))
print(f"Accuracy: {accuracy_score(y_val, y_pred):.4f}")


Evaluación del modelo XGBoost:
              precision    recall  f1-score   support

           0       0.96      0.77      0.85     68412
           1       0.16      0.55      0.24      5306

    accuracy                           0.75     73718
   macro avg       0.56      0.66      0.55     73718
weighted avg       0.90      0.75      0.81     73718

Accuracy: 0.7515


### 7.Modelo LightGBM 
- Cambiamos a LightGBM por problemas con los hiperparámetros de XGBoost ( tendríamos que realizar la búsqueda manualmente)

In [41]:
import pandas as pd
from lightgbm import LGBMClassifier
from sklearn.metrics import classification_report, accuracy_score

# Configurar el modelo básico
lgbm_model = LGBMClassifier(random_state=42)

# Entrenar el modelo
lgbm_model.fit(X_train, y_train)

# Predicciones en el conjunto de validación
y_pred = lgbm_model.predict(X_val)

# Evaluación del modelo
print("Evaluación del modelo LightGBM (básico):")
print(classification_report(y_val, y_pred))
print(f"Accuracy: {accuracy_score(y_val, y_pred):.4f}")


[LightGBM] [Info] Number of positive: 21273, number of negative: 273598
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003925 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2064
[LightGBM] [Info] Number of data points in the train set: 294871, number of used features: 12
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.072143 -> initscore=-2.554221
[LightGBM] [Info] Start training from score -2.554221
Evaluación del modelo LightGBM (básico):
              precision    recall  f1-score   support

           0       0.93      1.00      0.97     68412
           1       1.00      0.09      0.17      5306

    accuracy                           0.93     73718
   macro avg       0.97      0.55      0.57     73718
weighted avg       0.94      0.93      0.91     73718

Accuracy: 0.9348


#### Análisis del modelo básico LightGBM

**1. Métricas del modelo**

- **Clase 0 (no agregó al carrito):**
  - **Precisión**: 93% → Excelente.
  - **Recall**: 100% → Captura todos los ejemplos negativos correctamente.
  - **F1-Score**: 97% → Muy alto, pero influenciado por la clase dominante.

- **Clase 1 (agregó al carrito):**
  - **Precisión**: 100% → No predice falsos positivos.
  - **Recall**: 9% → Bajo, indicando que la mayoría de los positivos reales no son identificados.
  - **F1-Score**: 17% → Mejor que el modelo Random Forest inicial, pero aún limitado.

- **Accuracy global**:
  - **93.48%**: Similar al modelo Random Forest, dominado por la clase mayoritaria.

- **Macro Avg F1-Score**:
  - **57%**: Mejor que Random Forest debido a la precisión de la clase 1, pero el bajo recall de esta clase limita el impacto.

---

**2. Observaciones del entrenamiento**
- **Balance de clases**:
  - **21273 positivos vs. 273598 negativos** → La proporción desbalanceada sigue impactando el desempeño del modelo.
  - Esto es evidente en el bajo recall de la clase 1, ya que el modelo está sesgado hacia la clase 0.

- **Tiempo de entrenamiento**:
  - El modelo entrenó rápidamente, confirmando la eficiencia de LightGBM incluso con datasets más grandes.

---

**3. Comparación con XGBoost y Random Forest**
- Similar a XGBoost, el modelo **mejora el F1-Score** para la clase minoritaria (17% vs. 10% en Random Forest).
- Sin embargo, aún **sufre en recall** para la clase 1, lo cual es crítico para nuestro objetivo.

---

**Recomendaciones**

1. **Manejar el desbalance**:
   - Usar `class_weight='balanced'` o ajustar manualmente los pesos de las clases.
   - Alternativamente, experimentar con técnicas de oversampling (e.g., **SMOTE**) o undersampling.

2. **Hiperparámetros iniciales**:
   - Ajustar `scale_pos_weight` para mejorar el balance de la clase 1.
   - Investigar `learning_rate`, `max_depth`, y `num_leaves` para optimizar la generalización.

3. **Próximo paso**:
   - Ajustar los hiperparámetros usando **GridSearchCV** con un enfoque en mejorar el recall y F1-Score para la clase 1.



#### Ajuste de hipermarámetros
- `GridSearchCV` :  {'class_weight': None, 'colsample_bytree': 0.8, 'learning_rate': 0.01, 'max_depth': 9, 'n_estimators': 200, 'scale_pos_weight': 10, 'subsample': 0.8}

Vamos a implementar un ajuste de hiperparámetros utilizando GridSearchCV para explorar combinaciones clave que puedan mejorar el desempeño, especialmente en la clase minoritaria (clase 1).

In [42]:
from sklearn.model_selection import GridSearchCV
from lightgbm import LGBMClassifier

# Espacio de búsqueda para los hiperparámetros
param_grid = {
    'n_estimators': [50, 100, 200],          # Número de árboles
    'max_depth': [3, 6, 9],                 # Profundidad máxima
    'learning_rate': [0.01, 0.1, 0.3],      # Tasa de aprendizaje
    'class_weight': [None, 'balanced'],     # Peso de clases automático
    'subsample': [0.8, 1.0],                # Muestreo de filas
    'colsample_bytree': [0.8, 1.0],         # Muestreo de columnas
    'scale_pos_weight': [1, 5, 10]          # Peso manual para la clase minoritaria
}

# Configurar el modelo base
lgbm_base = LGBMClassifier(random_state=42)

# Configurar GridSearchCV
grid_search = GridSearchCV(
    estimator=lgbm_base,
    param_grid=param_grid,
    scoring='f1',
    cv=3,
    verbose=2,
    n_jobs=1  # Sin paralelización
)

# Ajustar el modelo
grid_search.fit(X_train, y_train)

# Extraer el mejor modelo y parámetros
best_model = grid_search.best_estimator_
print("Mejores parámetros encontrados:", grid_search.best_params_)

# Evaluar el mejor modelo en el conjunto de validación
from sklearn.metrics import classification_report, accuracy_score

y_pred_best = best_model.predict(X_val)
print("Evaluación del mejor modelo:")
print(classification_report(y_val, y_pred_best))
print(f"Accuracy: {accuracy_score(y_val, y_pred_best):.4f}")


Fitting 3 folds for each of 648 candidates, totalling 1944 fits
[LightGBM] [Info] Number of positive: 14182, number of negative: 182398
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.008025 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2062
[LightGBM] [Info] Number of data points in the train set: 196580, number of used features: 12
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.072144 -> initscore=-2.554218
[LightGBM] [Info] Start training from score -2.554218
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best g

In [43]:
# Extraer el mejor modelo y parámetros
best_model = grid_search.best_estimator_
print("Mejores parámetros encontrados:", grid_search.best_params_)

# Evaluar el mejor modelo en el conjunto de validación
from sklearn.metrics import classification_report, accuracy_score

y_pred_best = best_model.predict(X_val)
print("Evaluación del mejor modelo:")
print(classification_report(y_val, y_pred_best))
print(f"Accuracy: {accuracy_score(y_val, y_pred_best):.4f}")


Mejores parámetros encontrados: {'class_weight': None, 'colsample_bytree': 0.8, 'learning_rate': 0.01, 'max_depth': 9, 'n_estimators': 200, 'scale_pos_weight': 10, 'subsample': 0.8}


Evaluación del mejor modelo:
              precision    recall  f1-score   support

           0       0.95      0.85      0.90     68412
           1       0.19      0.45      0.27      5306

    accuracy                           0.82     73718
   macro avg       0.57      0.65      0.59     73718
weighted avg       0.90      0.82      0.86     73718

Accuracy: 0.8247


In [44]:
from joblib import dump, load

# Guardar el mejor modelo LightGBM
dump(best_model, "/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/models/hybrid/best_lightgbm_model.joblib")

# # Cargar el modelo guardado
# loaded_model = load("best_lightgbm_model.joblib")

['/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/models/hybrid/best_lightgbm_model.joblib']

#### Análisis hiperparámetros

**Resultados clave:**
1. **Mejores hiperparámetros encontrados**:
   - `learning_rate=0.01`: Un valor bajo, lo que indica un entrenamiento más lento pero cuidadoso para evitar el sobreajuste.
   - `max_depth=9`: Los árboles pueden explorar relaciones complejas sin ser excesivamente profundos.
   - `scale_pos_weight=10`: Refleja un reequilibrio de clases, dado el desbalance entre la clase mayoritaria (`0`) y la minoritaria (`1`).
   - `n_estimators=200`: Un valor conservador para iteraciones, lo que sugiere que el modelo podría beneficiarse de más iteraciones con un `learning_rate` bajo.

2. **Métricas**:
   - **Precisión global (Accuracy)**: **82.47%**. Buen resultado general, pero influido por el desbalance de clases.
   - **Clase mayoritaria (`0`)**:
     - Alta precisión (95%) y buen recall (85%), lo que muestra que el modelo identifica bien los negativos.
   - **Clase minoritaria (`1`)**:
     - **Precisión**: 19%. El modelo tiene dificultades para predecir verdaderos positivos sin incluir muchos falsos positivos.
     - **Recall**: 45%. Aunque no es alto, captura una cantidad decente de positivos reales.
     - **F1-Score**: 27%. Refleja el compromiso entre precisión y recall, pero queda espacio para mejorar.

3. **Distribución macro y weighted**:
   - **Macro avg**: Destaca el desequilibrio, con diferencias notables entre las clases.
   - **Weighted avg**: Más influenciada por la clase mayoritaria.

---

**Análisis y recomendaciones**:

1. **Balance de clases**:
   - **Observación**: El ajuste de `scale_pos_weight=10` ayudó, pero no fue suficiente para equilibrar completamente el modelo.
   - **Recomendación**:
     - Considera métodos adicionales para el manejo del desbalance, como:
       - Aumentar el peso de la clase minoritaria aún más (`scale_pos_weight`).
       - Oversampling (SMOTE) o undersampling durante el preprocesamiento.
       - Incrementar el número de estimadores (`n_estimators`) con el `learning_rate` bajo.

2. **Recall y precisión de la clase `1`**:
   - **Observación**: La clase minoritaria tiene un recall moderado pero precisión baja.
   - **Recomendación**:
     - Revisa las características más relevantes para la predicción de la clase `1`. ¿Podrían algunas características estar perdiendo importancia debido al preprocesamiento o los valores?
     - Ajusta `max_depth` y `min_child_weight` para permitir divisiones más específicas que beneficien a la clase `1`.

3. **Modelo final**:
   - Utiliza estos hiperparámetros para entrenar en el conjunto completo de datos y generar las predicciones finales.
   - Evalúa si integrar modelos híbridos (popularidad y contenido) mejora los resultados.

4. **Evaluación adicional**:
   - Calcula métricas más específicas, como el AUC-ROC o PR-AUC, para tener una idea más clara de cómo el modelo maneja ambas clases.

---

### 8. Modelo híbrido

### **Implementar el modelo híbrido**


1. **Componentes del modelo híbrido:**
   - **Colaborativo:** Usar técnicas como matrix factorization (SVD o ALS) o modelos de deep learning (NCF) para explotar patrones de interacciones usuario-producto.
   - **Basado en contenido:** Incorporar atributos de los productos (como color, sección, familia) y características del usuario (`R`, `F`, `M`, país).
   - **Popularidad:** Integrar rankings globales o por segmentos (e.g., país o categoría) para recomendar productos altamente demandados.

2. **Fusión de resultados:**
   - Combinar las predicciones de los tres enfoques utilizando técnicas como:
     - **Ponderación:** Asignar pesos a cada enfoque según su relevancia.
     - **Rank blending:** Mezclar rankings basados en la posición de cada producto.


### **Plan para el modelo híbrido**

1. **Modelo de Colaboración:**
   - Implementar un modelo basado en interacciones usuario-producto (e.g., SVD o NCF).
   - Entrenar y validar usando datos de interacción `user_id` y `partnumber` del dataset de entrenamiento.

2. **Modelo Basado en Contenido:**
   - Usar atributos de productos (color, sección, familia) y características del usuario (`R`, `F`, `M`, país).
   - Entrenar un modelo como LightGBM o un regresor logístico para predecir la probabilidad de interacción basada en atributos.

3. **Modelo de Popularidad:**
   - Generar un ranking global o segmentado por popularidad del producto (e.g., frecuencia de interacciones).

4. **Fusión de Resultados:**
   - Combinar las predicciones de los tres enfoques:
     - **Ponderación:** Ajustar pesos para cada enfoque según su relevancia.
     - **Rank blending:** Mezclar rankings según las posiciones de los productos.

5. **Evaluación:**
   - Usar métricas como precisión, recall y NDCG para validar el modelo híbrido y compararlo con enfoques individuales.


---

### **Modelo colaborativo**

In [15]:
from surprise import SVD, Dataset, Reader
from surprise.model_selection import train_test_split
from sklearn.metrics import ndcg_score
import pandas as pd
import numpy as np

# 1. Preparar los datos
# Usar datos de interacciones (user_id, partnumber, add_to_cart)
interactions = train_sample[['user_id', 'partnumber', 'add_to_cart']].copy()

# Surprise requiere un formato específico para cargar datos
reader = Reader(rating_scale=(0, 1))  # Rating binario (add_to_cart: 0 o 1)
data = Dataset.load_from_df(interactions, reader)

# Dividir en entrenamiento y validación
trainset, testset = train_test_split(data, test_size=0.2)

# 2. Entrenar el modelo SVD
model = SVD(n_factors=50, random_state=42)  # 50 dimensiones en el embedding
model.fit(trainset)

# 3. Predicciones para el conjunto de prueba
predictions = model.test(testset)

# Convertir predicciones a un formato utilizable
true_ratings = []
predicted_ratings = []

for uid, iid, true_r, est, _ in predictions:
    true_ratings.append(true_r)
    predicted_ratings.append(est)

# 4. Calcular NDCG usando scikit-learn
ndcg = ndcg_score([true_ratings], [predicted_ratings], k=5)
print(f"NDCG@5: {ndcg:.4f}")

# 5. Generar recomendaciones para cada usuario
def get_top_n_recommendations(predictions, n=5):
    # Ordenar predicciones por usuario
    top_n = {}
    for uid, iid, true_r, est, _ in predictions:
        if uid not in top_n:
            top_n[uid] = []
        top_n[uid].append((iid, est))

    # Seleccionar los n mejores productos por usuario
    for uid, user_ratings in top_n.items():
        user_ratings.sort(key=lambda x: x[1], reverse=True)
        top_n[uid] = [iid for iid, _ in user_ratings[:n]]

    return top_n

# Obtener las recomendaciones
recommendations = get_top_n_recommendations(predictions)


NDCG@5: 0.3304


In [16]:
from joblib import dump, load

# Guardar el modelo SVD
dump(model, "/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/models/hybrid/svd_model_colab.joblib")

['/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/models/hybrid/svd_model_colab.joblib']

El resultado obtenido de **NDCG@5: 0.3333** es un buen punto de partida para el modelo basado en filtrado colaborativo utilizando SVD. Sin embargo, aún hay espacio para mejorar la calidad de las recomendaciones. A continuación, te sugiero algunos pasos a seguir:

**Análisis del Resultado**
1. **Interpretación del NDCG:** 
   - Un valor de 0.3333 significa que el modelo está capturando cierta relevancia en las recomendaciones, pero no es óptimo. Un valor ideal estaría más cerca de 1.
   - Esto indica que, aunque el modelo puede identificar algunos elementos relevantes, podría no estar capturando completamente las preferencias de los usuarios.

2. **Posibles Causas:**
   - **Datos de Entrada:** Si el conjunto de datos es muy limitado (por ejemplo, solo la muestra), el modelo puede no estar aprendiendo patrones significativos.
   - **Hiperparámetros del Modelo:** Los valores predeterminados del modelo SVD pueden no ser ideales para los datos específicos.
   - **Desequilibrio de Datos:** Si hay pocas interacciones positivas (adiciones al carrito), el modelo podría no estar entrenándose correctamente.





##### Optimizar el Modelo SVD

In [60]:
from surprise import SVD, Dataset, Reader
from surprise.model_selection import GridSearchCV, train_test_split
from sklearn.metrics import ndcg_score
import pandas as pd
import numpy as np

# 1. Preparar los datos
# Usar datos de interacciones (user_id, partnumber, add_to_cart)
interactions = train_sample[['user_id', 'partnumber', 'add_to_cart']].copy()

# Surprise requiere un formato específico para cargar datos
reader = Reader(rating_scale=(0, 1))  # Rating binario (add_to_cart: 0 o 1)
data = Dataset.load_from_df(interactions, reader)

# Dividir en entrenamiento y validación
trainset, testset = train_test_split(data, test_size=0.2)

# 2. Optimizar el modelo SVD con GridSearchCV
param_grid = {
    'n_factors': [20, 50, 100],
    'lr_all': [0.002, 0.005, 0.01],
    'n_epochs': [20, 50, 100]
}

gs = GridSearchCV(SVD, param_grid, measures=['rmse'], cv=3, n_jobs=-1)
gs.fit(data)

# Obtener los mejores hiperparámetros
best_params = gs.best_params['rmse']
print(f"Mejores parámetros: {best_params}")

# Entrenar el modelo con los mejores parámetros
best_model = SVD(**best_params)
best_model.fit(trainset)

# 3. Predicciones para el conjunto de prueba
predictions = best_model.test(testset)

# Convertir predicciones a un formato utilizable
true_ratings = []
predicted_ratings = []

for uid, iid, true_r, est, _ in predictions:
    true_ratings.append(true_r)
    predicted_ratings.append(est)

# 4. Calcular NDCG usando scikit-learn
ndcg = ndcg_score([true_ratings], [predicted_ratings], k=5)
print(f"NDCG@5: {ndcg:.4f}")

# 5. Generar recomendaciones para cada usuario
def get_top_n_recommendations(predictions, n=5):
    # Ordenar predicciones por usuario
    top_n = {}
    for uid, iid, true_r, est, _ in predictions:
        if uid not in top_n:
            top_n[uid] = []
        top_n[uid].append((iid, est))

    # Seleccionar los n mejores productos por usuario
    for uid, user_ratings in top_n.items():
        user_ratings.sort(key=lambda x: x[1], reverse=True)
        top_n[uid] = [iid for iid, _ in user_ratings[:n]]

    return top_n

# Obtener las recomendaciones
recommendations = get_top_n_recommendations(predictions)
print(f"Recomendaciones generadas para los usuarios: {recommendations}")


Mejores parámetros: {'n_factors': 20, 'lr_all': 0.002, 'n_epochs': 20}
NDCG@5: 0.3077
Recomendaciones generadas para los usuarios: {0: [6988, 6988, 6988, 6988, 6988], 23390: [22927], 30399: [15417], 4653: [24177], 3435: [24170], 9080: [7386], 5589: [9470], 14505: [13952], 25785: [2160], 27858: [19564], 21753: [15884], 2801: [9308], 24700: [7900, 2627], 21758: [520], 17208: [13806], 26680: [12404, 4206], 34653: [17947, 5098], 30902: [14817], 40226: [7011], 33451: [22585], 38706: [17843], 22099: [24410], 21235: [14144], 35999: [16027], 13866: [15232], 31745: [14829], 29951: [12046], 2844: [18084], 19936: [6672], 4573: [11751], 11559: [12356], 33508: [17280], 5526: [18605], 20839: [7891], 12075: [15459], 40912: [11900], 27390: [24584], 39389: [10513], 20205: [1681], 9707: [10908], 30562: [18450, 19790], 37463: [4746], 22800: [15516], 24867: [2798], 25559: [14172, 17762], 19815: [21365], 2312: [12900], 24500: [7043], 18913: [4439], 23706: [8992], 31433: [6071], 30828: [5514], 41934: [6083]

#### Modelo NCF

In [7]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, Flatten, Concatenate, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from sklearn.metrics import ndcg_score

# Preparar los datos
user_id_map = {id_: idx for idx, id_ in enumerate(train_sample['user_id'].unique())}
partnumber_map = {id_: idx for idx, id_ in enumerate(train_sample['partnumber'].unique())}

train_sample['user_id_idx'] = train_sample['user_id'].map(user_id_map)
train_sample['partnumber_idx'] = train_sample['partnumber'].map(partnumber_map)

train_data, val_data = train_test_split(train_sample, test_size=0.2, random_state=42)

# Crear el modelo NCF
num_users = len(user_id_map)
num_items = len(partnumber_map)

user_input = Input(shape=(1,))
item_input = Input(shape=(1,))
user_embedding = Embedding(input_dim=num_users, output_dim=32)(user_input)
item_embedding = Embedding(input_dim=num_items, output_dim=32)(item_input)
user_vec = Flatten()(user_embedding)
item_vec = Flatten()(item_embedding)
concat = Concatenate()([user_vec, item_vec])
dense = Dense(128, activation='relu')(concat)
dropout = Dropout(0.5)(dense)
dense = Dense(64, activation='relu')(dropout)
output = Dense(1, activation='sigmoid')(dense)

ncf_model = Model(inputs=[user_input, item_input], outputs=output)
ncf_model.compile(optimizer=Adam(learning_rate=0.001), loss='binary_crossentropy', metrics=['accuracy'])

# Entrenar el modelo
train_users = train_data['user_id_idx'].values
train_items = train_data['partnumber_idx'].values
train_labels = train_data['add_to_cart'].values

val_users = val_data['user_id_idx'].values
val_items = val_data['partnumber_idx'].values
val_labels = val_data['add_to_cart'].values

ncf_model.fit(
    [train_users, train_items],
    train_labels,
    validation_data=([val_users, val_items], val_labels),
    epochs=5,
    batch_size=512,
    verbose=0  # Suprimir salida de entrenamiento
)

# Calcular NDCG
val_predictions = ncf_model.predict([val_users, val_items]).flatten()
ndcg = ndcg_score([val_labels], [val_predictions], k=5)
print(f"NDCG@5: {ndcg:.4f}")


2304/2304 ━━━━━━━━━━━━━━━━━━━━ 2s 999us/step
NDCG@5: 0.3156


In [8]:
from sklearn.metrics import precision_score, recall_score

# Función para calcular precision@k, recall@k y F1@k
def compute_metrics_at_k(true_labels, predicted_scores, k=5):
    # Obtener los índices de los productos con mayores predicciones
    top_k_indices = np.argsort(predicted_scores)[-k:][::-1]
    
    # Convertir predicciones top_k a etiquetas binarias
    top_k_predictions = np.zeros_like(predicted_scores)
    top_k_predictions[top_k_indices] = 1

    # Precision, Recall y F1
    precision = precision_score(true_labels, top_k_predictions, zero_division=0)
    recall = recall_score(true_labels, top_k_predictions, zero_division=0)
    f1 = 2 * (precision * recall) / (precision + recall + 1e-10)
    
    return precision, recall, f1

# Calcular métricas adicionales para el conjunto de validación
precision, recall, f1 = compute_metrics_at_k(val_labels, val_predictions, k=5)

# Reportar métricas
print(f"NDCG@5: {ndcg:.4f}")
print(f"Precision@5: {precision:.4f}")
print(f"Recall@5: {recall:.4f}")
print(f"F1@5: {f1:.4f}")


NDCG@5: 0.3156
Precision@5: 0.4000
Recall@5: 0.0004
F1@5: 0.0008


#### Modelo NCF + Hiperparámetros

Para optimizar los hiperparámetros del modelo NCF, utilizaremos un enfoque sistemático con un marco de búsqueda aleatoria o una búsqueda en malla para ajustar los siguientes parámetros clave:

1. **Dimensiones de los embeddings (`output_dim`)**: Probar diferentes tamaños para los embeddings de usuario y producto.
2. **Tasa de aprendizaje (`learning_rate`)**: Evaluar diferentes tasas para encontrar un equilibrio entre convergencia y estabilidad.
3. **Arquitectura de las capas densas**:
   - Número de unidades por capa.
   - Número de capas ocultas.
4. **Regularización (`dropout`)**: Ajustar el nivel de Dropout para reducir sobreajuste.
5. **Batch size (`batch_size`)**: Ajustar el tamaño de los lotes para optimizar el rendimiento del entrenamiento.

**Plan**

1. Implementar `RandomizedSearchCV` o una búsqueda manual para explorar combinaciones de hiperparámetros.
2. Evaluar las combinaciones con una métrica principal (NDCG@5) y métricas complementarias (Precisión, Recall, F1).
3. Registrar los resultados para identificar la configuración óptima.


In [10]:
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import ParameterGrid
import random

# Espacio de hiperparámetros
param_grid = {
    'embedding_dim': [16, 32, 64],
    'learning_rate': [0.001, 0.0005, 0.0001],
    'dense_units': [[128, 64], [256, 128, 64], [64]],
    'dropout_rate': [0.3, 0.5, 0.7],
    'batch_size': [256, 512, 1024],
}

# Obtener combinaciones de hiperparámetros
param_combinations = list(ParameterGrid(param_grid))
random.shuffle(param_combinations)  # Mezclar para búsqueda aleatoria

# Registro de resultados
results = []

# Entrenar y evaluar diferentes configuraciones
for i, params in enumerate(param_combinations[:10]):  # Limitar a las primeras 10 combinaciones
    print(f"Probando combinación {i+1}/{len(param_combinations)}: {params}")
    
    # Crear el modelo con los parámetros actuales
    user_embedding = Embedding(input_dim=num_users, output_dim=params['embedding_dim'])(user_input)
    item_embedding = Embedding(input_dim=num_items, output_dim=params['embedding_dim'])(item_input)
    user_vec = Flatten()(user_embedding)
    item_vec = Flatten()(item_embedding)
    concat = Concatenate()([user_vec, item_vec])

    dense = concat
    for units in params['dense_units']:
        dense = Dense(units, activation='relu')(dense)
        dense = Dropout(params['dropout_rate'])(dense)
    output = Dense(1, activation='sigmoid')(dense)

    ncf_model = Model(inputs=[user_input, item_input], outputs=output)
    ncf_model.compile(optimizer=Adam(learning_rate=params['learning_rate']), loss='binary_crossentropy', metrics=['accuracy'])

    # Entrenar el modelo
    ncf_model.fit(
        [train_users, train_items],
        train_labels,
        validation_data=([val_users, val_items], val_labels),
        epochs=5,
        batch_size=params['batch_size'],
        verbose=0  # Reducir la salida para múltiples experimentos
    )

    # Calcular métricas ajustadas
    val_predictions_sorted_idx = np.argsort(val_predictions)[::-1][:5]  # Índices de las 5 predicciones más altas
    top_k_labels = val_labels[val_predictions_sorted_idx]  # Etiquetas verdaderas para los 5 productos más recomendados

    precision = np.sum(top_k_labels) / len(top_k_labels)  # Proporción de productos relevantes en el top 5
    recall = np.sum(top_k_labels) / np.sum(val_labels)  # Proporción de productos relevantes recuperados
    f1 = 2 * (precision * recall) / (precision + recall + 1e-10)  # F1 Score

    ndcg = ndcg_score([val_labels], [val_predictions], k=5)

    # Registrar resultados
    results.append({
        'params': params,
        'ndcg@5': ndcg,
        'precision@5': precision,
        'recall@5': recall,
        'f1@5': f1,
    })

    print(f"NDCG@5: {ndcg:.4f}, Precision@5: {precision:.4f}, Recall@5: {recall:.4f}, F1@5: {f1:.4f}")

# Ordenar por NDCG@5
results = sorted(results, key=lambda x: x['ndcg@5'], reverse=True)

# Mostrar la mejor combinación
print(f"Mejor combinación de parámetros: {results[0]['params']}")
print(f"Métricas: {results[0]}")


Probando combinación 1/243: {'batch_size': 1024, 'dense_units': [128, 64], 'dropout_rate': 0.5, 'embedding_dim': 16, 'learning_rate': 0.001}


2025-01-11 00:37:49.964570: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_57', 24 bytes spill stores, 24 bytes spill loads

2025-01-11 00:37:50.542549: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_57', 32 bytes spill stores, 32 bytes spill loads

2025-01-11 00:37:50.571301: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_57', 12 bytes spill stores, 12 bytes spill loads



NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 2/243: {'batch_size': 1024, 'dense_units': [64], 'dropout_rate': 0.5, 'embedding_dim': 64, 'learning_rate': 0.001}


2025-01-11 00:37:56.587107: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_900', 224 bytes spill stores, 224 bytes spill loads



NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 3/243: {'batch_size': 1024, 'dense_units': [64], 'dropout_rate': 0.7, 'embedding_dim': 64, 'learning_rate': 0.001}
NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 4/243: {'batch_size': 1024, 'dense_units': [64], 'dropout_rate': 0.3, 'embedding_dim': 64, 'learning_rate': 0.001}
NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 5/243: {'batch_size': 1024, 'dense_units': [64], 'dropout_rate': 0.5, 'embedding_dim': 16, 'learning_rate': 0.0001}
NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 6/243: {'batch_size': 1024, 'dense_units': [128, 64], 'dropout_rate': 0.3, 'embedding_dim': 16, 'learning_rate': 0.001}
NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 7/243: {'batch_size': 1024, 'dense_units': [64], 'dropout_rate': 0.7, 'embedding_dim': 32

2025-01-11 00:38:31.963429: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_57', 24 bytes spill stores, 24 bytes spill loads

2025-01-11 00:38:32.834048: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_57', 12 bytes spill stores, 12 bytes spill loads



NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 9/243: {'batch_size': 1024, 'dense_units': [64], 'dropout_rate': 0.3, 'embedding_dim': 16, 'learning_rate': 0.0005}
NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Probando combinación 10/243: {'batch_size': 256, 'dense_units': [64], 'dropout_rate': 0.3, 'embedding_dim': 64, 'learning_rate': 0.001}
NDCG@5: 0.1461, Precision@5: 0.2000, Recall@5: 0.0002, F1@5: 0.0004
Mejor combinación de parámetros: {'batch_size': 1024, 'dense_units': [128, 64], 'dropout_rate': 0.5, 'embedding_dim': 16, 'learning_rate': 0.001}
Métricas: {'params': {'batch_size': 1024, 'dense_units': [128, 64], 'dropout_rate': 0.5, 'embedding_dim': 16, 'learning_rate': 0.001}, 'ndcg@5': 0.1460683498427064, 'precision@5': 0.2, 'recall@5': 0.00018846588767433095, 'f1@5': 0.0003765769156469482}


#### Modelo NCF Optimizado

In [11]:
from tensorflow.keras.regularizers import l2

# Crear el modelo NCF optimizado
def create_optimized_ncf(num_users, num_items, embedding_dim, dense_units, dropout_rate, l2_reg):
    user_input = Input(shape=(1,))
    item_input = Input(shape=(1,))
    
    # Embeddings con regularización L2
    user_embedding = Embedding(input_dim=num_users, output_dim=embedding_dim, embeddings_regularizer=l2(l2_reg))(user_input)
    item_embedding = Embedding(input_dim=num_items, output_dim=embedding_dim, embeddings_regularizer=l2(l2_reg))(item_input)
    
    user_vec = Flatten()(user_embedding)
    item_vec = Flatten()(item_embedding)
    
    # Concatenación
    concat = Concatenate()([user_vec, item_vec])
    
    # Capas densas con dropout y regularización
    dense = Dense(dense_units[0], activation='relu', kernel_regularizer=l2(l2_reg))(concat)
    dense = Dropout(dropout_rate)(dense)
    
    for units in dense_units[1:]:
        dense = Dense(units, activation='relu', kernel_regularizer=l2(l2_reg))(dense)
        dense = Dropout(dropout_rate)(dense)
    
    output = Dense(1, activation='sigmoid')(dense)
    
    model = Model(inputs=[user_input, item_input], outputs=output)
    model.compile(optimizer=Adam(learning_rate=0.001), loss='binary_crossentropy', metrics=['accuracy'])
    
    return model

# Entrenamiento
ncf_model = create_optimized_ncf(
    num_users=num_users,
    num_items=num_items,
    embedding_dim=32,
    dense_units=[128, 64],
    dropout_rate=0.5,
    l2_reg=0.01
)

ncf_model.fit(
    [train_users, train_items],
    train_labels,
    validation_data=([val_users, val_items], val_labels),
    epochs=10,
    batch_size=512,
    verbose=1
)


Epoch 1/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 4s 5ms/step - accuracy: 0.9045 - loss: 2.7084 - val_accuracy: 0.9280 - val_loss: 0.2610
Epoch 2/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.9280 - loss: 0.2672 - val_accuracy: 0.9280 - val_loss: 0.2598
Epoch 3/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 2s 3ms/step - accuracy: 0.9286 - loss: 0.2644 - val_accuracy: 0.9280 - val_loss: 0.2591
Epoch 4/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 2s 3ms/step - accuracy: 0.9274 - loss: 0.2668 - val_accuracy: 0.9280 - val_loss: 0.2590
Epoch 5/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.9284 - loss: 0.2635 - val_accuracy: 0.9280 - val_loss: 0.2590
Epoch 6/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.9283 - loss: 0.2632 - val_accuracy: 0.9280 - val_loss: 0.2589
Epoch 7/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.9287 - loss: 0.2618 - val_accuracy: 0.9280 - val_loss: 0.2590
Epoch 8/10
576/576 ━━━━━━━━━━━━━━━━━━━━ 3s 3ms/step - accuracy: 0.9275 - loss: 0.2640 - val_accuracy: 0.

In [13]:
def calculate_metrics(val_labels, val_predictions, k=5):
    # Crear un diccionario para almacenar rankings por usuario
    user_ranks = {}
    for idx, (user, label, prediction) in enumerate(zip(val_users, val_labels, val_predictions)):
        if user not in user_ranks:
            user_ranks[user] = []
        user_ranks[user].append((label, prediction))

    # Inicializar métricas
    ndcg, precision, recall = 0, 0, 0
    total_users = len(user_ranks)

    # Calcular métricas para cada usuario
    for user, ranks in user_ranks.items():
        # Ordenar los productos por predicción
        ranks.sort(key=lambda x: x[1], reverse=True)
        labels = [x[0] for x in ranks]
        predictions = [x[1] for x in ranks]

        # NDCG
        if len(labels) > 1:  # Asegurarse de que hay más de un documento
            ndcg += ndcg_score([labels], [predictions], k=k)
        
        # Precision y Recall
        precision += sum(labels[:k]) / k
        recall += sum(labels[:k]) / sum(labels) if sum(labels) > 0 else 0

    # Promediar las métricas
    ndcg /= total_users
    precision /= total_users
    recall /= total_users
    f1 = 2 * (precision * recall) / (precision + recall + 1e-10)

    return ndcg, precision, recall, f1

# Calcular métricas
ndcg, precision, recall, f1 = calculate_metrics(val_labels, val_predictions, k=5)

# Imprimir métricas
print(f"NDCG@5: {ndcg:.4f}, Precision@5: {precision:.4f}, Recall@5: {recall:.4f}, F1@5: {f1:.4f}")


NDCG@5: 0.0039, Precision@5: 0.0186, Recall@5: 0.0923, F1@5: 0.0309


### **Modelo basado en contenido**

#### **Plan para el modelo basado en contenido**



1. **Preparación de datos:**
   - Combinar los datasets de usuarios y productos con las interacciones.
   - Generar un dataset con las características necesarias para el modelo.
   - Imputar valores faltantes y escalar las variables numéricas.

2. **Entrenamiento del modelo:**
   - Usar un modelo como **LightGBM**, **XGBoost**, o una red neuronal para predecir la probabilidad de interacción.
   - Realizar optimización de hiperparámetros para mejorar el rendimiento.

3. **Evaluación del modelo:**
   - Evaluar el modelo con métricas como AUC, F1-score y NDCG@5.

4. **Guardar el modelo:**
   - Guardar el modelo entrenado para su integración en el pipeline híbrido.

In [45]:
product_path = '/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/data/processed/new_processed/products_data.pkl'
user_path = '/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/data/processed/new_processed/user_data.csv'

import pandas as pd

# Cargar los datasets
products_data = pd.read_pickle(product_path)
users_data = pd.read_csv(user_path)

#### 1. Preparación de los datos

In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer

# Cargar datasets
users = users_data.copy()
products = products_data.copy()
interactions = train_sample.copy()

# Combinar datasets
data = interactions.merge(users, on="user_id", how="left")
data = data.merge(products, on="partnumber", how="left")

# Seleccionar características relevantes
features = ['R', 'F', 'M', 'country', 'color_id', 'cod_section', 'family', 'discount']
target = 'add_to_cart'

# Imputar valores faltantes
imputer = SimpleImputer(strategy='median')
data[features] = imputer.fit_transform(data[features])

# Escalar características numéricas
scaler = StandardScaler()
data[features] = scaler.fit_transform(data[features])

# Dividir en entrenamiento y validación
X = data[features]
y = data[target]

X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)


#### 2. Entrenamiento del modelo

In [ ]:
from lightgbm import LGBMClassifier

# Configurar el modelo
content_model = LGBMClassifier(random_state=42, n_estimators=100, learning_rate=0.1)

# Entrenar el modelo
content_model.fit(X_train, y_train, eval_set=[(X_val, y_val)], eval_metric='auc', early_stopping_rounds=10, verbose=True)


#### 3. Evaluación del modelo

In [ ]:
from sklearn.metrics import classification_report, roc_auc_score

# Predicciones
y_pred = content_model.predict(X_val)
y_pred_prob = content_model.predict_proba(X_val)[:, 1]

# Evaluar métricas
print("AUC:", roc_auc_score(y_val, y_pred_prob))
print("Reporte de clasificación:")
print(classification_report(y_val, y_pred))


#### 4. Guardado del modelo

In [ ]:
from joblib import dump

# Guardar el modelo basado en contenido
dump(content_model, "content_based_model.joblib")


### **Modelo de Popularidad**

#### Plan

Este modelo se centra en recomendar productos basados en su popularidad general o segmentada. Algunos enfoques que podemos considerar:

1. **Popularidad global**:
   - Contar las interacciones (`add_to_cart`) por producto en todo el conjunto de entrenamiento.
   - Ordenar los productos por frecuencia y recomendar los más populares.

2. **Popularidad segmentada**:
   - Calcular la popularidad dentro de segmentos específicos (por ejemplo, por `country`, `cod_section` o `family`).
   - Recomendaciones personalizadas basadas en el segmento del usuario.

3. **Decay Temporal** (opcional):
   - Considerar que la popularidad puede cambiar con el tiempo.
   - Dar más peso a interacciones recientes.

#### Popularidad global

In [47]:
# Calcular popularidad global
popularidad_global = train_sample.groupby('partnumber')['add_to_cart'].sum().sort_values(ascending=False)

# Obtener los productos más populares
top_n_global = popularidad_global.index[:10].tolist()
print("Productos más populares globalmente:", top_n_global)


Productos más populares globalmente: [11074, 9498, 14971, 15920, 19296, 6988, 23900, 6996, 7651, 14263]


#### Popularidad segmentada por country

In [57]:
# Calcular popularidad por país
popularidad_por_pais = train_sample.groupby(['country', 'partnumber'])['add_to_cart'].sum()

# Función para obtener recomendaciones por país
def recomendaciones_por_pais(country, top_n=5):
    if country in popularidad_por_pais.index.get_level_values(0):
        productos = popularidad_por_pais[country].sort_values(ascending=False).index[:top_n]
        return productos.tolist()
    else:
        return top_n_global  # Si no hay datos para el país, usar popularidad global

# Ejemplo de recomendaciones para un país específico
recs_country = recomendaciones_por_pais(country=1)
print(f"Recomendaciones para el país 1: {recs_country}")


Recomendaciones para el país 1: [11074, 9498, 14971, 15920, 19296, 6988, 23900, 6996, 7651, 14263]


#### Decay Temporal (opcional)

In [58]:
# Calcular popularidad ajustada por tiempo de forma explícita
train_sample['weighted_interaction'] = train_sample['add_to_cart'] * train_sample['decay_weight']
popularidad_decay = train_sample.groupby('partnumber')['weighted_interaction'].sum().sort_values(ascending=False)

# Obtener los productos más populares ajustados por tiempo
top_n_decay = popularidad_decay.index[:10].tolist()
print("Productos más populares (ajustados temporalmente):", top_n_decay)




Productos más populares (ajustados temporalmente): [11074, 6988, 14213, 9844, 5886, 4453, 6013, 19744, 7973, 14971]


---

## Implementación modelo hibrido

In [67]:
import joblib
import pandas as pd

# 1. Cargar el modelo colaborativo (SVD)
svd_model = joblib.load("/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/models/hybrid/svd_model_colab.joblib")

# 2. Cargar el modelo basado en contenido (LightGBM)
lgbm_model = joblib.load("/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/models/hybrid/best_lightgbm_model.joblib")

# 3. Cargar datos de popularidad
global_popularity = [11074, 9498, 14971, 15920, 19296, 6988, 23900, 6996, 7651, 14263] 
temporal_popularity = [11074, 6988, 14213, 9844, 5886, 4453, 6013, 19744, 7973, 14971] 

print("Modelos cargados correctamente.")

Modelos cargados correctamente.


Ajuste de datasets

In [73]:
product_path = '/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/data/processed/new_processed/products_data.pkl'
user_path = '/home/pablost/Hackathon_inditex_data_science/hackathon-inditex-data-recommender/data/processed/new_processed/user_data.csv'

import pandas as pd

# Cargar los datasets
products = pd.read_pickle(product_path)
users = pd.read_csv(user_path)

In [75]:
print(users.head())
print(users.columns)


   user_id  country         R         F         M
0   430096       25  0.016438  0.000558  0.000001
1   134018       25  0.060274  0.002976  0.000003
2    53750       25  0.001826  0.005951  0.000003
3   180665       25  0.020091  0.002046  0.000003
4   134209       25  0.006393  0.000186  0.000003
Index(['user_id', 'country', 'R', 'F', 'M'], dtype='object')


In [76]:
print(train_sample['user_id'].dtype)
print(users['user_id'].dtype)


int64
int64


In [82]:
train_sample.columns

Index(['session_id', 'date', 'timestamp_local', 'add_to_cart', 'user_id',
       'country', 'partnumber', 'device_type', 'pagetype', 'session_length',
       'unique_products_count', 'product_popularity', 'time_of_day',
       'time_diff', 'country_popularity', 'device_popularity', 'decay_weight',
       'weighted_interaction', 'timestamp_scaled', 'R', 'F', 'M', 'discount'],
      dtype='object')

In [85]:
test.columns

Index(['session_id', 'date', 'timestamp_local', 'user_id', 'country',
       'partnumber', 'device_type', 'pagetype', 'session_length',
       'unique_products_count', 'product_popularity', 'time_of_day',
       'time_diff', 'country_popularity', 'device_popularity'],
      dtype='object')

#### Alinear test con las características del modelo

In [86]:
# Merge con el dataset de usuarios para R, F, M
test = test.merge(users[['user_id', 'R', 'F', 'M']], on='user_id', how='left')

# Imputar valores faltantes de R, F, M con 0
test[['R', 'F', 'M']] = test[['R', 'F', 'M']].fillna(0)

# Merge con el dataset de productos para discount
test = test.merge(products[['partnumber', 'discount']], on='partnumber', how='left')

# Imputar valores faltantes de discount con 0
test['discount'] = test['discount'].fillna(0)

# Confirmar que el test contiene las columnas necesarias
required_columns = ['R', 'F', 'M', 'discount', 'session_length', 
                    'unique_products_count', 'product_popularity', 
                    'time_of_day', 'time_diff', 'country_popularity', 
                    'device_popularity']

# Asegurar que no haya valores faltantes en las columnas requeridas
for col in required_columns:
    if col not in test.columns:
        test[col] = 0  # Agregar columnas faltantes con valores por defecto
    else:
        test[col] = test[col].fillna(0)


In [87]:
# Crear test_features con las columnas relevantes
test_features = test[required_columns + ['user_id', 'partnumber']]


In [ ]:
import numpy as np
import pandas as pd
import json

# Columnas requeridas
required_columns = ['session_id', 'user_id', 'country', 'partnumber', 'device_type', 'pagetype', 
                    'session_length', 'unique_products_count', 'product_popularity', 
                    'country_popularity', 'device_popularity', 'time_of_day', 'time_diff']

# Imputar columnas faltantes en test_features
print("Imputando columnas faltantes en test_features...")
for col in required_columns:
    if col not in test_features.columns:
        if col in test.columns:
            # Si está en test original, agregarla
            test_features[col] = test[col]
        else:
            # Imputar valores predeterminados si no está disponible
            if col in ['session_length', 'unique_products_count', 'product_popularity', 
                       'country_popularity', 'device_popularity', 'time_diff']:
                test_features[col] = 0  # Valores numéricos predeterminados
            elif col in ['country', 'device_type', 'pagetype', 'time_of_day']:
                test_features[col] = 'unknown'  # Valores categóricos predeterminados
            else:
                test_features[col] = None  # Para session_id, user_id y partnumber

# Codificar columnas categóricas
categorical_columns = ['country', 'device_type', 'pagetype', 'time_of_day']
print("Codificando columnas categóricas...")
for col in categorical_columns:
    if col in test_features:
        test_features[col] = test_features[col].astype('category').cat.codes

# Asegurar orden de columnas
test_features = test_features[required_columns]

# Validación final
missing_columns = [col for col in required_columns if col not in test_features.columns]
if missing_columns:
    raise ValueError(f"Las siguientes columnas siguen faltando en test_features: {missing_columns}")

print("test_features está listo con todas las columnas necesarias.")

# 2. Generar predicciones individuales
print("Generando predicciones individuales...")

# SVD (colaborativo)
print("Generando predicciones SVD...")
testset_svd = list(zip(test_features['user_id'], test_features['partnumber'], np.zeros(len(test_features))))
svd_predictions = svd_model.test(testset_svd)
svd_df = pd.DataFrame([(pred.uid, pred.iid, pred.est) for pred in svd_predictions], 
                      columns=['user_id', 'partnumber', 'svd_score'])

# LightGBM (basado en contenido)
print("Generando predicciones LightGBM...")
lgbm_predictions = lgbm_model.predict_proba(test_features.drop(columns=['session_id']))[:, 1]
lgbm_df = pd.DataFrame({'user_id': test_features['user_id'], 
                        'partnumber': test_features['partnumber'], 
                        'lgbm_score': lgbm_predictions})

# Popularidad
print("Generando predicciones basadas en popularidad...")
popular_partnumbers = [p for p in global_popularity if p in test_features['partnumber'].unique()]
popularity_scores = np.linspace(1, 0, len(popular_partnumbers))
popularity_df = pd.DataFrame({
    'partnumber': popular_partnumbers,
    'popularity_score': popularity_scores
})

# 3. Fusionar predicciones en un solo DataFrame
print("Fusionando predicciones...")
merged_df = svd_df.merge(lgbm_df, on=['user_id', 'partnumber'], how='outer')
merged_df = merged_df.merge(popularity_df, on='partnumber', how='outer')

# 4. Imputar valores faltantes
print("Imputando valores faltantes...")
merged_df['svd_score'] = merged_df['svd_score'].fillna(0)
merged_df['lgbm_score'] = merged_df['lgbm_score'].fillna(0)
merged_df['popularity_score'] = merged_df['popularity_score'].fillna(0)

# 5. Combinar predicciones con pesos
print("Calculando puntajes finales...")
weights = {'svd': 0.5, 'lgbm': 0.3, 'popularity': 0.2}
merged_df['final_score'] = (
    merged_df['svd_score'] * weights['svd'] +
    merged_df['lgbm_score'] * weights['lgbm'] +
    merged_df['popularity_score'] * weights['popularity']
)

# 6. Generar recomendaciones finales para cada sesión
print("Generando recomendaciones finales...")
def get_hybrid_recommendations(session_id, n=5):
    user_data = test_features[test_features['session_id'] == session_id]
    user_recommendations = merged_df[
        merged_df['user_id'].isin(user_data['user_id']) &
        merged_df['partnumber'].isin(user_data['partnumber'])
    ]
    if user_recommendations.empty:
        return list(dict.fromkeys(global_popularity[:n]))  # Respaldo: productos más populares únicos
    top_products = user_recommendations.sort_values('final_score', ascending=False).head(n)
    return list(dict.fromkeys(top_products['partnumber'].tolist()))

recommendations = {}
for session_id in test_features['session_id'].unique():
    recommendations[session_id] = get_hybrid_recommendations(session_id)
    if len(recommendations[session_id]) < 5:
        recommendations[session_id].extend(global_popularity[:5 - len(recommendations[session_id])])

# Convertir claves a string para compatibilidad con JSON
recommendations_str_keys = {str(session_id): recs for session_id, recs in recommendations.items()}

# 7. Salida JSON
output_path = "predictions_3.json"
with open(output_path, 'w') as file:
    json.dump({"target": recommendations_str_keys}, file)

print(f"Archivo JSON generado correctamente en {output_path}")


In [ ]:
import numpy as np
import pandas as pd
import json

# Confirmar que LightGBM usa GPU
print("Configurando LightGBM para usar GPU...")
lgbm_model.set_params(device='gpu')  # Configurar para GPU
print("LightGBM configurado para GPU.")

# Columnas requeridas
required_columns = ['session_id', 'user_id', 'country', 'partnumber', 'device_type', 'pagetype', 
                    'session_length', 'unique_products_count', 'product_popularity', 
                    'country_popularity', 'device_popularity', 'time_of_day', 'time_diff']

# Imputar columnas faltantes en test_features
print("Imputando columnas faltantes en test_features...")
for col in required_columns:
    if col not in test_features.columns:
        if col in test.columns:
            # Si está en test original, agregarla
            test_features[col] = test[col]
        else:
            # Imputar valores predeterminados si no está disponible
            if col in ['session_length', 'unique_products_count', 'product_popularity', 
                       'country_popularity', 'device_popularity', 'time_diff']:
                test_features[col] = 0  # Valores numéricos predeterminados
            elif col in ['country', 'device_type', 'pagetype', 'time_of_day']:
                test_features[col] = 'unknown'  # Valores categóricos predeterminados
            else:
                test_features[col] = None  # Para session_id, user_id y partnumber

# Codificar columnas categóricas
print("Codificando columnas categóricas...")
categorical_columns = ['country', 'device_type', 'pagetype', 'time_of_day']
for col in categorical_columns:
    if col in test_features:
        test_features[col] = test_features[col].astype('category').cat.codes

# Asegurar orden de columnas
print("Asegurando que las columnas están en el orden esperado...")
test_features = test_features[required_columns]

# Validación final
missing_columns = [col for col in required_columns if col not in test_features.columns]
if missing_columns:
    raise ValueError(f"Las siguientes columnas siguen faltando en test_features: {missing_columns}")

print("test_features está listo con todas las columnas necesarias.")

# 2. Generar predicciones individuales
print("Generando predicciones SVD (colaborativo)...")
testset_svd = list(zip(test_features['user_id'], test_features['partnumber'], np.zeros(len(test_features))))
svd_predictions = svd_model.test(testset_svd)

# Convertir predicciones SVD a un DataFrame
print("Convirtiendo predicciones SVD a DataFrame...")
svd_df = pd.DataFrame([(pred.uid, pred.iid, pred.est) for pred in svd_predictions], 
                      columns=['user_id', 'partnumber', 'svd_score'])

# LightGBM (basado en contenido)
print("Generando predicciones LightGBM (contenido)...")
lgbm_predictions = lgbm_model.predict_proba(test_features.drop(columns=['session_id']))[:, 1]
lgbm_df = pd.DataFrame({'user_id': test_features['user_id'], 
                        'partnumber': test_features['partnumber'], 
                        'lgbm_score': lgbm_predictions})

# Popularidad
print("Calculando puntajes de popularidad...")
popular_partnumbers = [p for p in global_popularity if p in test_features['partnumber'].unique()]
popularity_scores = np.linspace(1, 0, len(popular_partnumbers))

popularity_df = pd.DataFrame({
    'partnumber': popular_partnumbers,
    'popularity_score': popularity_scores
})

# 3. Fusionar predicciones en un solo DataFrame
print("Fusionando predicciones en un solo DataFrame...")
merged_df = svd_df.merge(lgbm_df, on=['user_id', 'partnumber'], how='outer')
merged_df = merged_df.merge(popularity_df, on='partnumber', how='outer')

# 4. Imputar valores faltantes
print("Imputando valores faltantes en el DataFrame fusionado...")
merged_df['svd_score'] = merged_df['svd_score'].fillna(0)
merged_df['lgbm_score'] = merged_df['lgbm_score'].fillna(0)
merged_df['popularity_score'] = merged_df['popularity_score'].fillna(0)

# 5. Combinar predicciones con pesos
print("Calculando puntajes finales combinados...")
weights = {'svd': 0.5, 'lgbm': 0.3, 'popularity': 0.2}
merged_df['final_score'] = (
    merged_df['svd_score'] * weights['svd'] +
    merged_df['lgbm_score'] * weights['lgbm'] +
    merged_df['popularity_score'] * weights['popularity']
)

# 6. Generar recomendaciones finales para cada sesión
def get_hybrid_recommendations(session_id, n=5):
    user_data = test_features[test_features['session_id'] == session_id]
    user_recommendations = merged_df[
        merged_df['user_id'].isin(user_data['user_id']) &
        merged_df['partnumber'].isin(user_data['partnumber'])
    ]
    if user_recommendations.empty:
        return global_popularity[:n]  # Respaldo: productos más populares
    top_products = user_recommendations.sort_values('final_score', ascending=False).head(n)
    return list(set(top_products['partnumber'].tolist()))

print("Generando recomendaciones para todos los session_id...")
recommendations = {}
for session_id in test_features['session_id'].unique():
    recommendations[session_id] = get_hybrid_recommendations(session_id)

# Convertir claves a string para compatibilidad con JSON
recommendations_str_keys = {str(session_id): recs for session_id, recs in recommendations.items()}

# 7. Salida JSON
output_path = "predictions_3.json"
print(f"Guardando predicciones en {output_path}...")
with open(output_path, 'w') as file:
    json.dump({"target": recommendations_str_keys}, file)

print(f"Archivo JSON generado correctamente en {output_path}")
